# **Pipline Causal Analysis**

In [2]:
! pip install -q datasets
! pip install -q ydata-profiling
! pip install -q transformers
! pip install -q --upgrade openai
! pip install -q huggingface_hub
! pip install scikit-learn torch

^C
ERROR: Operation cancelled by user


In [38]:
! ollama pull llama2:7b-chat-q4_0
! ollama pull llama2:7b-chat-q5_0
! ollama pull llama2:7b-chat-q8_0
! ollama pull llama2:7b-chat-fp16
! ollama pull llama2:13b-chat-q4_0
! ollama pull llama2:13b-chat-q5_0
! ollama pull llama2:13b-chat-q8_0
! ollama pull llama2:13b-chat-fp16

pulling manifest ⠋ pulling manifest ⠙ pulling manifest ⠹ pulling manifest ⠸ pulling manifest ⠼ pulling manifest ⠴ pulling manifest ⠦ pulling manifest 
pulling 8934d96d3f08... 100% ▕████████████████▏ 3.8 GB                         
pulling 8c17c2ebb0ea... 100% ▕████████████████▏ 7.0 KB                         
pulling 7c23fb36d801... 100% ▕████████████████▏ 4.8 KB                         
pulling 2e0493f67d0c... 100% ▕████████████████▏   59 B                         
pulling fa304d675061... 100% ▕████████████████▏   91 B                         
pulling 42ba7f8a01dd... 100% ▕████████████████▏  557 B                         
verifying sha256 digest ⠋ pulling manifest 
pulling 8934d96d3f08... 100% ▕████████████████▏ 3.8 GB                         
pulling 8c17c2ebb0ea... 100% ▕████████████████▏ 7.0 KB                         
pulling 7c23fb36d801... 100% ▕████████████████▏ 4.8 KB                         
pulling 2e0493f67d0c... 100% ▕████████████████▏   59 B                         
pulli

In [1]:
import pandas as pd
from datasets import load_from_disk

# Word embedding test
from sklearn.metrics.pairwise import cosine_similarity
from transformers import AutoTokenizer, AutoModel
import torch
import numpy as np
import requests
import pandas as pd
from sklearn.metrics.pairwise import cosine_similarity
from langchain import PromptTemplate

pd.set_option("display.max_columns", 1000)
pd.set_option("display.max_rows", 20)
pd.set_option("max_colwidth", 1000)

/home/lujun/anaconda3/envs/causalLLM/lib/python3.9/site-packages/transformers/utils/generic.py:441: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(


Data Preparation - Take only 300 for the testing

In [2]:
local_dataset_path = "../resource/data/databricks-dolly-15k"
dataset = load_from_disk(local_dataset_path)
df = dataset.to_pandas()
test_df = df[df["category"] == "closed_qa"]
test = test_df.head(300)

In [4]:
def calculate_cosine_similarity(text, groundtruth, model_name="bert-base-uncased"):
    tokenizer = AutoTokenizer.from_pretrained(model_name)
    model = AutoModel.from_pretrained(model_name)

    input_ids_text = tokenizer.encode(text, return_tensors="pt")
    input_ids_groundtruth = tokenizer.encode(groundtruth, return_tensors="pt")

    with torch.no_grad():
        embeddings_text = model(input_ids_text)[0].squeeze().numpy()
        embeddings_groundtruth = model(input_ids_groundtruth)[0].squeeze().numpy()

    similarity_text = cosine_similarity(embeddings_text, embeddings_groundtruth)[0, 0]
    return similarity_text


def generate_response(df_row, api_url="http://localhost:11434/api/generate"):
    model_tag = str(df_row["model_tag"])
    prompt = str(df_row["prompt"])
    temperature = df_row["temperature"]
    payload = {
        "model": model_tag,
        "prompt": prompt,
        "stream": False,
        "options": {"temperature": temperature},
    }
    api_response = requests.post(api_url, json=payload)
    try:
        api_data = api_response.json()
        response = api_data["response"]
        return response
    except Exception as e:
        print(f"Error processing API response: {e}")
        return None

In [13]:
import json

url = "http://localhost:11434/api/generate"

columns_list = [
    "model",
    "ground_truth" "created_at",
    "response",
    "done",
    "prompt",
    "instruction",
    "context",
    "category",
    "quantization",
    "temperature",
    "context_repetition",
    "accuracy",
]

result_df = pd.DataFrame(columns=columns_list)
instruction = """Please strictly answer the question based on the context I gave to you. If the question cannot be answered using the information provided answer with "I don't know". """
template = """

Instruction: {instruction}

Context: {context}

Question: {question}

"""
prompt_template = PromptTemplate.from_template(template)
columns = [
    "temperature",
    "context_repetition",
    "model",
    "quantization_bits",
    "model_tag",
    "question",
    "context",
    "ground_truth_response",
    "prompt",
    "payload",
]
result_df = pd.DataFrame(columns=columns)

In [14]:
for context_repetition in range(1, 3):
    for index, row in test.iterrows():
        question = row["instruction"]
        context = row["context"] * context_repetition
        response = row["response"]
        category = row["category"]

        prompt = prompt_template.format(
            instruction=instruction, context=context, question=question
        )

        for model in ["7b", "13b"]:
            for q in ["-chat-q4_0", "-chat-q5_0", "-chat-q8_0", "-chat-fp16"]:
                for temperature in np.arange(0.1, 1, 0.2):
                    model_tag = "llama2:" + model + q
                    data = {
                        "temperature": temperature,
                        "context_repetition": context_repetition,
                        "model": "llama" + model,
                        "quantization_bits": q,
                        "model_tag": model_tag,
                        "question": question,
                        "context": context,
                        "ground_truth_response": response,
                        "prompt": str(prompt),
                    }
                    result_df = pd.concat(
                        [result_df, pd.DataFrame([data])], ignore_index=True
                    )

1


/tmp/ipykernel_182709/4268382322.py:28: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  result_df = pd.concat(


2


In [5]:
# result_df.to_excel("job_1.xlsx")
loaded_df = pd.read_excel("job_1.xlsx")


def extract_random_row(group):
    return group.sample(10)


result_df = loaded_df.groupby("model_tag", group_keys=False).apply(extract_random_row)
result_df = result_df.reset_index(drop=True)
result_df = result_df[~result_df["model_tag"].str.contains("fp")]

In [8]:
from tqdm import tqdm

pbar = tqdm(total=len(result_df))
responses = []
similarities = []
for index, row in result_df.iterrows():
    response = generate_response(row)
    similarity = calculate_cosine_similarity(response, row["ground_truth_response"])
    responses.append(response)
    pbar.update(1)
result_df["generated_response"] = responses
result_df["cosine_similarity"] = similarities
pbar.close()

100%|██████████| 60/60 [1:03:01<00:00, 63.02s/it]


KeyboardInterrupt: 

In [20]:
from nltk.translate.bleu_score import sentence_bleu, SmoothingFunction
from sklearn.metrics import precision_score, recall_score, f1_score

similarities = []
for index, row in result_df.iterrows():
    response = row["generated_response"]
    similarity = calculate_cosine_similarity(response, row["ground_truth_response"])
    similarities.append(similarity)
result_df["cosine_similarity"] = similarities

smooth = SmoothingFunction()
ground_truth_responses = result_df["ground_truth_response"].tolist()
generated_responses = result_df["generated_response"].tolist()

# Calculate Precision, Recall, and F1-score
threshold = 0.8  # You can adjust the threshold based on your cosine similarity values
binary_similarities = [1 if sim > threshold else 0 for sim in similarities]

bleu_scores = [
    round(
        sentence_bleu([ref.split()], gen.split(), smoothing_function=smooth.method1), 2
    )
    for ref, gen in zip(ground_truth_responses, generated_responses)
]

result_df["bleu_score"] = bleu_scores
result_df.to_excel("result_job_1.xlsx")

In [17]:
result_df.to_excel("result_job_1.xlsx")

In [15]:
result_df.to_excel("result_job_1.xlsx")

In [14]:
result_df.columns

Index(['Unnamed: 0', 'temperature', 'context_repetition', 'model',
       'quantization_bits', 'model_tag', 'question', 'context',
       'ground_truth_response', 'prompt', 'payload', 'generated_response',
       'cosine_similarity'],
      dtype='object')